In [ ]:
# First, install the base packages
!pip install --no-cache-dir torch torchvision torchaudio

# Install huggingface hub first since it's a dependency for many packages
!pip install --no-cache-dir huggingface-hub==0.23.0

# Install transformers next since it's also a common dependency
!pip install --no-cache-dir transformers==4.41.0

# Now install the main packages we need
!pip install --no-cache-dir diffusers==0.21.4
!pip install --no-cache-dir controlnet_aux==0.0.7
!pip install --no-cache-dir accelerate
!pip install --no-cache-dir xformers
!pip install --no-cache-dir safetensors
!pip install --no-cache-dir opencv-python mediapipe

# Verify our installations
import torch
print(f"PyTorch version: {torch.__version__}")

# Import our key libraries
from diffusers import StableDiffusionControlNetPipeline, ControlNetModel
from controlnet_aux import OpenposeDetector
print("All imports successful!")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 401.2/401.2 kB 21.1 MB/s eta 0:00:00
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.26.2
    Uninstalling huggingface-hub-0.26.2:
      Successfully uninstalled huggingface-hub-0.26.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
diffusers 0.31.0 requires huggingface-hub>=0.23.2, but you have huggingface-hub 0.23.0 which is incompatible.
transformers 4.46.2 requires huggingface-hub<1.0,>=0.23.2, but you have huggingface-hub 0.23.0 which is incompatible.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.8/43.8 kB 40.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.1/9.1 MB 98.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 317.4 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.20.3
   

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

All imports successful!


/usr/local/lib/python3.10/dist-packages/timm/models/layers/__init__.py:48: FutureWarning: Importing from timm.models.layers is deprecated, please import via timm.layers
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.layers", FutureWarning)
/usr/local/lib/python3.10/dist-packages/timm/models/registry.py:4: FutureWarning: Importing from timm.models.registry is deprecated, please import via timm.models
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.models", FutureWarning)
/usr/local/lib/python3.10/dist-packages/controlnet_aux/segment_anything/modeling/tiny_vit_sam.py:654: UserWarning: Overwriting tiny_vit_5m_224 in registry with controlnet_aux.segment_anything.modeling.tiny_vit_sam.tiny_vit_5m_224. This is because the name being registered conflicts with an existing name. Please check if this is not expected.
  return register_model(fn_wrapper)
/usr/local/lib/python3.10/dist-packages/controlnet_aux/segment_anything/mode

In [ ]:
# Import necessary libraries
import cv2
import numpy as np
from PIL import Image
import os
import requests
import torch
from tqdm.notebook import tqdm
from diffusers import StableDiffusionControlNetPipeline, ControlNetModel
from controlnet_aux import OpenposeDetector

def download_video(url, filename, max_retries=3):
    """
    Downloads a video with progress tracking and retry capability.
    This function includes error handling and will attempt multiple downloads if needed.
    """
    print("Starting video download...")
    for attempt in range(max_retries):
        try:
            response = requests.get(url, stream=True, timeout=30)
            response.raise_for_status()

            # Get total file size for progress bar
            total_size = int(response.headers.get('content-length', 0))
            block_size = 1024
            progress_bar = tqdm(total=total_size, unit='iB', unit_scale=True)

            with open(filename, 'wb') as file:
                for data in response.iter_content(block_size):
                    progress_bar.update(len(data))
                    file.write(data)
            progress_bar.close()

            print(f"Successfully downloaded video to {filename}")
            return True

        except Exception as e:
            print(f"Attempt {attempt + 1} failed: {str(e)}")
            if attempt + 1 == max_retries:
                raise Exception(f"Failed to download video after {max_retries} attempts")
            print("Retrying download...")

def extract_frames(video_path, frame_interval=1):
    """
    Extracts and processes frames from a video file at specified intervals.
    Includes progress tracking and converts frames to RGB format for AI processing.

    Args:
        video_path (str): Path to the video file
        frame_interval (int): Extract every Nth frame (1 = every frame, 2 = every other frame, etc.)
    """
    if not os.path.exists(video_path):
        raise FileNotFoundError(f"Video file not found: {video_path}")

    print("Extracting frames from video...")
    frames = []
    cap = cv2.VideoCapture(video_path)

    if not cap.isOpened():
        raise ValueError("Failed to open video file")

    # Get video properties
    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = cap.get(cv2.CAP_PROP_FPS)
    duration = total_frames / fps

    print(f"Video properties:")
    print(f"- Total frames: {total_frames}")
    print(f"- FPS: {fps}")
    print(f"- Duration: {duration:.2f} seconds")
    print(f"- Frame interval: {frame_interval} (processing every {frame_interval}th frame)")

    frame_count = 0
    progress_bar = tqdm(total=total_frames // frame_interval, desc="Extracting frames")

    while True:
        ret, frame = cap.read()
        if not ret:
            break

        if frame_count % frame_interval == 0:
            # Convert BGR to RGB for compatibility with AI models
            frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            frames.append(frame_rgb)
            progress_bar.update(1)

        frame_count += 1

    cap.release()
    progress_bar.close()

    print(f"Successfully extracted {len(frames)} frames")
    return frames, fps

def get_output_fps(original_fps, frame_interval):
    """Calculate the output FPS based on the frame interval"""
    return original_fps / frame_interval

# Main execution block with comprehensive error handling
try:
    # Check hardware capabilities and set up appropriate device
    print("Checking GPU availability...")
    use_gpu = torch.cuda.is_available()
    device = "cuda" if use_gpu else "cpu"
    print(f"Using device: {device}")

    # Download the video
    video_url = "https://videos.pexels.com/video-files/4727645/4727645-uhd_2560_1440_25fps.mp4"
    input_filename = "input_video.mp4"
    download_video(video_url, input_filename)

    # Calculate appropriate frame interval based on device
    frame_interval = 2 if use_gpu else 4  # Process every 2nd frame on GPU, every 4th frame on CPU

    # Extract frames with calculated interval
    frames, original_fps = extract_frames(input_filename, frame_interval=frame_interval)
    output_fps = get_output_fps(original_fps, frame_interval)

    # Initialize AI models with appropriate settings for the device
    print("Initializing AI models...")
    pose_detector = OpenposeDetector.from_pretrained("lllyasviel/ControlNet")
    controlnet = ControlNetModel.from_pretrained(
        "lllyasviel/sd-controlnet-openpose",
        torch_dtype=torch.float16 if use_gpu else torch.float32
    )

    # Initialize the main pipeline
    pipe = StableDiffusionControlNetPipeline.from_pretrained(
        "runwayml/stable-diffusion-v1-5",
        controlnet=controlnet,
        torch_dtype=torch.float16 if use_gpu else torch.float32,
        safety_checker=None
    )

    # Apply optimizations based on available hardware
    if use_gpu:
        pipe.enable_xformers_memory_efficient_attention()
        pipe.enable_model_cpu_offload()
    else:
        print("Running on CPU - some optimizations will be disabled")

    pipe.to(device)

    # Process frames and generate new images
    generated_frames = []
    prompt = "A stylized anime character dancing in a beautiful garden, high quality, detailed"

    print("Processing frames...")
    for i, frame in enumerate(tqdm(frames, desc="Generating images")):
        # Extract pose from frame
        pose_image = pose_detector(frame)

        # Generate new image based on pose
        generated_image = pipe(
            prompt,
            pose_image,
            negative_prompt="lowres, bad anatomy, worst quality, blurry",
            num_inference_steps=15 if use_gpu else 10,  # Adjust steps based on device
            generator=torch.manual_seed(42)
        ).images[0]

        generated_frames.append(np.array(generated_image))

        # Save intermediate results periodically
        if (i + 1) % 10 == 0:
            print(f"\nProcessed {i + 1}/{len(frames)} frames")

    # Save the results as a video
    if generated_frames:
        print("Creating output video...")
        height, width = generated_frames[0].shape[:2]
        fourcc = cv2.VideoWriter_fourcc(*'mp4v')
        output_filename = 'output.mp4'

        out = cv2.VideoWriter(
            output_filename,
            fourcc,
            output_fps,  # Use calculated output FPS
            (width, height)
        )

        for frame in tqdm(generated_frames, desc="Writing video"):
            frame_bgr = cv2.cvtColor(frame, cv2.COLOR_RGB2BGR)
            out.write(frame_bgr)
        out.release()

        print(f"Video generation completed!")
        print(f"Output video properties:")
        print(f"- Number of frames: {len(generated_frames)}")
        print(f"- FPS: {output_fps}")
        print(f"- Duration: {len(generated_frames) / output_fps:.2f} seconds")
        print(f"- Saved as: {output_filename}")

        # Save sample images for verification
        pose_image = pose_detector(frames[0])
        pose_image.save('sample_pose.png')
        Image.fromarray(generated_frames[0]).save('sample_generated.png')

except Exception as e:
    print(f"An error occurred: {str(e)}")
    import traceback
    traceback.print_exc()

print("Process completed!")

Checking GPU availability...
Using device: cuda
Starting video download...


  0%|          | 0.00/24.8M [00:00<?, ?iB/s]

Successfully downloaded video to input_video.mp4
Extracting frames from video...
Video properties:
- Total frames: 608
- FPS: 25.0
- Duration: 24.32 seconds
- Frame interval: 2 (processing every 2th frame)


Extracting frames:   0%|          | 0/304 [00:00<?, ?it/s]

Successfully extracted 304 frames
Initializing AI models...


...

  0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

Creating output video...


Writing video:   0%|          | 0/304 [00:00<?, ?it/s]

Video generation completed!
Output video properties:
- Number of frames: 304
- FPS: 12.5
- Duration: 24.32 seconds
- Saved as: output.mp4
Process completed!
